# `e3nn.o3.Irreps` and how to decompose your data into them with `e3nn.io.CartesianTensor` and friends.

Irreducible representations or irreps are the "datatypes" of `e3nn`. All inputs, outputs, and intermediate data in `e3nn` must be completely specificed in terms of how the data decomposes into irreps. Specifying the irreps defines how the piece of data transforms under the group of 3D rotations and parity (inversion), $SO(3) \times \mathbb{Z}_2 = O(3)$.

To specify an irrep of $O(3)$ you need two numbers it's degree $L$, which specifies its angular frequency, and parity $p$, whether or not the quantity changes sign under inversion. Each irrep is composed of $2 L + 1$ components which are further indexed by the order $m$. We denote these irreps as $L_p$ where $p$ is $e$ if even (1) under parity and $o$ if odd (-1) under parity.

We can instantiate the `o3.Irrep` class using these two numbers, `o3.Irrep(L, p)`.

In [1]:
import e3nn
from e3nn import o3, io
import torch

scalar = o3.Irrep(0, 1)
print(scalar)
# Invariant under rotation, invariant under parity.

pseudoscalar = o3.Irrep(0, -1)
print(pseudoscalar)
# Invariant under rotation, equivariant under parity.

vector = o3.Irrep(1, -1)
print(vector)
# Equivariant with same angular frequency as global rotation, equivariant under parity.

pseudovector = o3.Irrep(1, 1)
print(pseudovector)
# Equivariant with same angular frequency as global rotation, invariant under parity.

0e
0o
1o
1e


Most data involes multiple irreps or a direct sum of irreps, denoted mathematically with $\oplus$. We denote direct sums of multiple `o3.Irrep` classes with the `o3.Irreps` class. We can create `o3.Irreps` in many ways.

In [2]:
print(scalar + scalar + vector + pseudovector)
print(o3.Irreps('1x0e+1x0e+1x1o+1x1e'))
print(o3.Irreps([scalar, scalar, vector, pseudovector]))

scalar + scalar + vector + pseudovector == o3.Irreps('1x0e+1x0e+1x1o+1x1e') == o3.Irreps([scalar, scalar, vector, pseudovector])

1x0e+1x0e+1x1o+1x1e
1x0e+1x0e+1x1o+1x1e
1x0e+1x0e+1x1o+1x1e


True

While direct sums of irreps are mathematically sets, in our implementation they are ordered lists where grouping matters. Distinct terms in the `o3.Irreps` are treated differently in equivariant operations in for example `o3.TensorProduct` which we will discuss in a later tutorial.

In [3]:
print(4 * scalar) 
print(o3.Irreps(4 * [scalar]))
4 * scalar == o3.Irreps(4 * [scalar])

4x0e
1x0e+1x0e+1x0e+1x0e


False

The irreps class has several helpful attributes and methods

In [4]:
irreps = 4 * vector
# The dimension (e.g the size of the torch.tensor needed for to represent these irreps)
print('Dimension of irreps: ', irreps.dim)
# The number of distinct irreps.
print('Number of irreps: ', irreps.num_irreps)

Dimension of irreps:  12
Number of irreps:  4


## Irreps of Spherical Harmonics
Spherical harmonics have parity equal to $(-1)^{L}$. This is easiest to see if you plot them. Ones that look the same under inversion $(x, y, z) \rightarrow (-x, -y, -z)$ are even $(1)$ and those that look different are odd $(-1)$.

In [5]:
lmax = 4
o3.Irreps.spherical_harmonics(lmax)

1x0e+1x1o+1x2e+1x3o+1x4e

In [6]:
import plotly
from plotly.subplots import make_subplots
import plotly.graph_objects as go

lmax = 2
# Plots a scalar signal on the sphere
# p_val is the parity of the scalar (1 scalar, -1 pseudoscalar)
# p_arg is the parity of the unit vector (-1 vector, 1 pseudovector)
sph = io.SphericalTensor(lmax, p_val=1, p_arg=-1)

rows = lmax + 1
cols = 2 * lmax + 1
specs = [[{'is_3d': True} for i in range(cols)]
         for j in range(rows)]
fig = make_subplots(rows=rows, cols=cols, specs=specs)

diag = torch.eye(sph.dim)
trace_kwargs = sph.plotly_surface(diag, res=50)

for l in range(lmax + 1):
    offset = lmax - l + 1
    row_kwargs = trace_kwargs[l ** 2: (l + 1)**2] 
    traces = [go.Surface(**kwargs, showlegend=False, showscale=False) for kwargs in row_kwargs]
    fig.add_traces(traces, rows=[l + 1]*(2 * l + 1), cols=[offset + i for i in range(2 * l + 1)])
fig.update_layout(scene_aspectmode='data')

## Cartesian vectors and Cartesian tensors
We use an irrep convention such that `o3.Irrep(1o)` transforms as $(x, y, z)$. In fact, our irreps are similar to [real spherical harmonics](https://en.wikipedia.org/wiki/Table_of_spherical_harmonics#Real_spherical_harmonics) where $(y, z, x) \rightarrow (x, y, z)$.

For higher-rank Cartesian tensors, we need a change of basis matrix to convert from Cartesian indices to a single irrep index. To obtain the transformation matrix we can use the `e3nn.io.CartesianTensor` which inherits from `o3.Irreps`.

In [12]:
io.CartesianTensor('i').change_of_basis() # [yzx, xyz]

tensor([[1., 0., 0.],
        [0., 1., 0.],
        [0., 0., 1.]])

We can generalize this to higher order Cartesian tensors.

In [14]:
# 3x3 matrix
rank2 = io.CartesianTensor('ij')
print('Matrix \t\t\t', rank2, '\t\t {} degrees of freedom'.format(rank2.dim))

# 3x3 symmmetric matrix
symm_rank2 = io.CartesianTensor('ij=ji')
print('Symmmetric matrix \t', symm_rank2, '\t\t\t {} degrees of freedom'.format(symm_rank2.dim))

# 3x3 antisymmmetric matrix
antisymm_rank2 = io.CartesianTensor('ij=-ji')
print('Antisymmmetric matrix \t', antisymm_rank2, '\t\t\t\t {} degrees of freedom'.format(antisymm_rank2.dim))

# rank 4 symmetric tensor (e.g. elasticity tensor)
symm_rank4 = io.CartesianTensor('ijkl=jikl=klij')
print('Symmetric Rank 4 \t', symm_rank4, '\t\t {} degrees of freedom'.format(symm_rank4.dim))

Matrix 			 1x0e+1x1e+1x2e 		 9 degrees of freedom
Symmmetric matrix 	 1x0e+1x2e 			 6 degrees of freedom
Antisymmmetric matrix 	 1x1e 				 3 degrees of freedom
Symmetric Rank 4 	 2x0e+2x2e+1x4e 		 21 degrees of freedom


### Transformation matrices Q are not unique! 
They can differ by sign and even weighting if you have multiple copies of a given `o3.Irrep`.

In [17]:
assert torch.allclose(io.CartesianTensor('ij').change_of_basis(), io.CartesianTensor('ij').change_of_basis())
assert torch.allclose(io.CartesianTensor('ij').change_of_basis(), io.CartesianTensor('ij').change_of_basis())
assert torch.allclose(io.CartesianTensor('ij').change_of_basis(), io.CartesianTensor('ij').change_of_basis())

<b>If you use a Q matrix to prepare your data, it's important that you save the object that you use with your data, for example with...</b>

In [20]:
cartesian_tensor = io.CartesianTensor('ij')
Q = cartesian_tensor.change_of_basis()
torch.save(cartesian_tensor.change_of_basis(), 'Q.torch')
Q_loaded = torch.load('Q.torch')
torch.allclose(Q, Q_loaded)

True